In [13]:
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path
from pyaxis import pyaxis
import matplotlib.font_manager as fm 
from matplotlib.lines import Line2D
from matplotlib.patches import Patch

In [14]:
# Load the "Jost" font needed for this plot
font_dir = ['./Jost_Font/']  # Font is located in Jost_Font folder
for font in fm.findSystemFonts(font_dir):
    fm.fontManager.addfont(font)

In [15]:
gpd.options.io_engine = "pyogrio"

In [16]:
data = pd.read_csv("./language_per_municipality.csv", sep=';')

In [17]:
data.head()

GEO_ID            GEO_NAME       VARIABLE  VALUE           UNIT STATUS  \
0       1     Aeugst am Albis  Sprachgebiete      1  Sprachgebiete      A   
1       2  Affoltern am Albis  Sprachgebiete      1  Sprachgebiete      A   
2       3          Bonstetten  Sprachgebiete      1  Sprachgebiete      A   
3       4     Hausen am Albis  Sprachgebiete      1  Sprachgebiete      A   
4       5            Hedingen  Sprachgebiete      1  Sprachgebiete      A   

     STATUS_DESC                DESC_VAL  PERIOD_REF  \
0  Normaler Wert  Deutsches Sprachgebiet  2020-01-01   
1  Normaler Wert  Deutsches Sprachgebiet  2020-01-01   
2  Normaler Wert  Deutsches Sprachgebiet  2020-01-01   
3  Normaler Wert  Deutsches Sprachgebiet  2020-01-01   
4  Normaler Wert  Deutsches Sprachgebiet  2020-01-01   

                                              SOURCE LAST_UPDATE GEOM_CODE  \
0  BFS – Raumgliederungen der Schweiz, Strukturer...  2022-12-20      polg   
1  BFS – Raumgliederungen der Schweiz, Strukturer...  2022-12-20      polg   
2  BFS – Raumgliederungen der Schweiz, Strukturer...  2022-12-20      polg   
3  BFS – Raumgliederungen der Schweiz, Strukturer...  2022-12-20      polg   
4  BFS – Raumgliederungen der Schweiz, Strukturer...  2022-12-20      polg   

                   GEOM GEOM_PERIOD  MAP_ID  \
0  Politische Gemeinden  2022-05-01   26599   
1  Politische Gemeinden  2022-05-01   26599   
2  Politische Gemeinden  2022-05-01   26599   
3  Politische Gemeinden  2022-05-01   26599   
4  Politische Gemeinden  2022-05-01   26599   

                                             MAP_URL  
0  https://www.atlas.bfs.admin.ch/maps/13/map/map...  
1  https://www.atlas.bfs.admin.ch/maps/13/map/map...  
2  https://www.atlas.bfs.admin.ch/maps/13/map/map...  
3  https://www.atlas.bfs.admin.ch/maps/13/map/map...  
4  https://www.atlas.bfs.admin.ch/maps/13/map/map...

In [18]:
border_layout_folder = Path("./boundaries")
municipality_border = border_layout_folder / "k4g23.shx"
canton_border = border_layout_folder / "k4k23.shx"

In [19]:
map_canton = gpd.read_file(str(canton_border))
map_municipality = gpd.read_file(str(municipality_border))

In [20]:
map_municipality = map_municipality.rename(columns={'GMDNAME': 'GEO_NAME'})
map_municipality = map_municipality.merge(data, on="GEO_NAME")

In [21]:
# from matplotlib.colors import LinearSegmentedColormap

# cmap = LinearSegmentedColormap.from_list(name="my_cmap", 
#                                                 colors=["darkred", "indianred", "white", "limegreen", "darkgreen"], N=6)

In [22]:
legend_elements_negative = [
       Patch(facecolor='#900303', label='> 16%'),
       Patch(facecolor='#c44a4a', label='8—16%'),
       Patch(facecolor='#eebdbd', label='0—8%'),
]

legend_elements_positive = [
       Patch(facecolor='#006311', label='> 16%'),
       Patch(facecolor='#02b639', label='8—16%'),
       Patch(facecolor='#a8eaaf', label='0—8%'),
]

legend_kwargs = {
       'prop': {'family': 'Jost', 'size': 18, 'weight': 'regular'}, 
       'labelcolor': 'dimgrey', 
       'framealpha': 0, 
       'labelspacing': 0.1, 
       'handlelength': 1.5, 
       'handleheight': 1, 
       'handletextpad': 0.4,
}

arrowprops = {
       'arrowstyle': 'Simple',
       'edgecolor': 'white',
       'facecolor': 'black',
       'linewidth': 1.5,
}


In [23]:
participation_without_ai = sorted_by_participation.loc[sorted_by_participation.KTNR != 16]

highest = sorted_by_participation.tail(1)
lowest_overall = sorted_by_participation.head(1)
lowest_without_ai = participation_without_ai.head(1)

annotation_items = {
    f'{highest["gemeinde_bezeichnung"].values[0]}, {highest["kanton_abbr"].values[0]}': [highest, (0.55, 0.1)],
    f'{lowest_overall["gemeinde_bezeichnung"].values[0]}, {lowest_overall["kanton_abbr"].values[0]}': [lowest_overall, (0.9, 0.9)],
    f'{lowest_without_ai["gemeinde_bezeichnung"].values[0]}, {lowest_without_ai["kanton_abbr"].values[0]}': [lowest_without_ai, (0.1, 0.85)]
}

NameError: name 'sorted_by_participation' is not defined

In [ ]:
def do_annotations(axis):
    for key, item in annotation_items.items():
        axis.annotate(
            key,
            xy=(item[0]['geometry'].centroid.x, item[0]['geometry'].centroid.y), xycoords='data',
            xytext=item[1], textcoords='axes fraction',
            size=30, va="center", ha="center",
            arrowprops={'connectionstyle': "arc3,rad=-0.2", **arrowprops},
            fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'}
        )
        
        text_x = item[1][0]
        text_y = item[1][1]
        text_y = text_y + 0.025 if text_y >= 0.5 else text_y - 0.025
        municipality_participation = item[0]['wahlbeteiligung'].values[0]
        participation_difference = municipality_participation - avg_participation
        color = '#006311' if participation_difference >= 0 else '#900303'
        axis.text(text_x - 0.02, text_y, f"{municipality_participation:.1f}%", fontproperties={'family': 'Jost', 'size': 20, 'weight': 'regular'}, horizontalalignment='center', verticalalignment='center', transform=axis.transAxes)
        axis.text(text_x + 0.02, text_y, f"({'+' if participation_difference >= 0 else '–'}{abs(municipality_participation - avg_participation):.1f}%)", color=color, fontproperties={'family': 'Jost', 'size': 20, 'weight': 'semibold'}, horizontalalignment='center', verticalalignment='center', transform=axis.transAxes)

In [24]:
# Create figure and axis
f, ax = plt.subplots(figsize=(36, 27), dpi=300)
p = map_municipality.plot(column="DESC_VAL", ax=ax, linewidth=1, edgecolor='white', legend=True)#, cmap=cmap)
map_canton.plot(ax=ax, linewidth=3.5, edgecolor='black', color=(0, 0, 0, 0))

ax.tick_params(which='both', bottom=False, top=False, right=False, left=False, labelleft=False, labelbottom=False) 

ax.spines.bottom.set_visible(False)
ax.spines.top.set_visible(False)
ax.spines.left.set_visible(False)
ax.spines.right.set_visible(False)

# do_annotations(ax)

# f.legend(handles=legend_elements_negative, bbox_to_anchor=(0.3205, 0.85), **legend_kwargs)
# f.legend(handles=legend_elements_positive, bbox_to_anchor=(0.2605, 0.85), **legend_kwargs)

# Set title
f.suptitle('Language Area Affiliation per Municipality', fontproperties={'family': 'Jost', 'size': 60, 'weight': 'bold'}, x=0.37, y=0.9)

# Set subtitle (there might be a better way, but I could not find a way to have differently colored text in one object...)
# f.text(x=0.157, y=0.85, s=f"Difference —              and               — in voter participation, compared to the", 
#        color='dimgrey', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'regular'})
# f.text(x=0.2181, y=0.85, s="positive", color='#006311', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
# f.text(x=0.2782, y=0.85, s="negative", color='#900303', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
# f.text(x=0.508, y=0.85, s=f"Swiss average of {avg_participation:.1f}%", color='black', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})

# f.text(x=0.8, y=0.175, s="Sources: bfs.admin.ch", color='dimgrey', fontproperties={'family': 'Jost', 'size': 18, 'weight': 'semibold'})

# Save the figure -> the output "plot.png" looks a lot closer to the original than the one displayed in this notebook
plt.savefig('language_regions.png', bbox_inches='tight', pad_inches=0.5)